# Project : Social Network Analysis

Author: Geethasree Madiraju Nagaraju  
Date: 05/21/2023


In this project, you will be given two social network networks, one small and one large, and be asked
to build spreadsheet models to solve some problems some typically SNA problem. The files are in
Excel file SocialNetworks.xlsx in sheets Small and Large. The Small sheet contains a social
network with 25 individuals and the Large sheet contains a social network with 50 individuals. For
each individuals, in sequence, the links that they have in the network are given. For example, in
the Large network, individual 9 is connected with individuals 7,8,26, and 29. You are to answer
each of the following questions for each of the networks.


In [3]:
import sys
import os
 
if 'google.colab' in sys.modules:
    !pip install idaes-pse --pre
    !idaes get-extensions --to ./bin
    os.environ['PATH'] += ':bin'

import numpy as np
import pandas as pd
import math
import matplotlib.pyplot as plt
from pyomo.environ import *

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 46.8/46.8 MB 19.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 11.9/11.9 MB 121.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 294.0/294.0 kB 31.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.6/49.6 kB 5.0 MB/s eta 0:00:00
Getting files...
Done
---------------------------------------------------
IDAES Extensions Build Versions
Solvers:  vno version file found
Library:  vno version file found


In [5]:
from google.colab import drive
drive.mount('/content/drive')
data_path = "/content/drive/MyDrive/Colab Notebooks/SocialNetworks.xlsx"

Mounted at /content/drive


In [70]:
# Read Graph data from xlsx into Adjacency Matrix
small_network = pd.read_excel(data_path,sheet_name='Small',header=None)
large_network = pd.read_excel(data_path,sheet_name='Large',header=None)
n_individuals_small = small_network.shape[0]
n_individuals_large = large_network.shape[0]
adj_mat_small = np.zeros((n_individuals_small,n_individuals_small))
adj_mat_large = np.zeros((n_individuals_large,n_individuals_large))
print(small_network.shape)
print(large_network.shape)

(20, 7)
(50, 10)


In [71]:
# Read into Adjacency Matrix - small network
for i in range(n_individuals_small):
  for j in [2,3,4,5,6]:
    conn = small_network.loc[i][j]
    if math.isnan(conn):
      break
    else:
      adj_mat_small[i,int(conn-1)] = 1

# Read into Adjacency Matrix - large network
for i in range(n_individuals_large):
  for j in [2,3,4,5,6,7,8,9]:
    conn = large_network.loc[i][j]
    if math.isnan(conn):
      break
    else:
      adj_mat_large[i,int(conn-1)] = 1


# Problem 1.a

* Density of the network = number of links in the network/number of all possible links  
* number of possible all links among $n$ nodes = $n.(n-1)/2 $ for an undirected graph

In [72]:
# Density of the small network - Since adjacency matrix is symmetric, all the connections will be double counted
density = np.sum(adj_mat_small)/((n_individuals_small**2) - n_individuals_small)
print("Density of the small network: ",density)

# Density of the large network
density = np.sum(adj_mat_large)/((n_individuals_large**2) - n_individuals_large)
print("Density of the large network: ",density)

Density of the small network:  0.15789473684210525
Density of the large network:  0.08163265306122448


# Problem 1.b - Shortest Path
* Fewest number of connections between two nodes in a network = number of connections in the shortest path between source node and destination node = length of shortest path - 1.

In [73]:
# declaring source and destination nodes between which shortest path need to be found out(based on zero indexing)
source_node = 0
destination_node = 15

### Small Network

In [74]:
#Create a Model
model = ConcreteModel()

#Variables
model.x = Var(range(n_individuals_small),range(n_individuals_small),within=Binary)

# Objective Function
objective_expr = 0
for i in range(n_individuals_small):
  for j in range(n_individuals_small):
    objective_expr += model.x[i,j]*adj_mat_small[i,j]

model.objective_expr = Objective(expr=objective_expr,sense=minimize)

# Constraints
# There cannot exist a path between nodes that are not connected
model.does_not_exist_constraints = ConstraintList()
for i in range(n_individuals_small):
  for j in range(n_individuals_small):
    if adj_mat_small[i,j] < 0.001:
      model.does_not_exist_constraints.add(model.x[i,j] == 0)

#Node flow constraints
#for all the intermediate nodes : number of outgoing edges - number of incoming edges = 0
# for source node : number of outgoing edges - number of incoming edges = 1
# for destination node : number of outgoing edges - number of incoming edges = -1
model.node_flow = ConstraintList()
for i in range(n_individuals_small):
  node_incoming_total = 0
  node_outgoing_total = 0
  for j in range(n_individuals_small):
    node_outgoing_total += model.x[i,j]
    node_incoming_total += model.x[j,i]
  if i==source_node:
    model.node_flow.add(node_outgoing_total-node_incoming_total == 1)
  elif i==destination_node:
    model.node_flow.add(node_outgoing_total-node_incoming_total == -1)
  else:
    model.node_flow.add(node_outgoing_total-node_incoming_total == 0)


model.pprint()

SolverFactory('cbc').solve(model, tee=True).write()

5 Set Declarations
    does_not_exist_constraints_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :  340 : {1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183, 184, 185, 

In [75]:
#print the shortest path from source to destination
for i in range(n_individuals_small):
  for j in range(n_individuals_small):
    if model.x[i,j]() > 0.5:
      print(i+1, "-->", j+1)
print("Shortest Path length: ",model.objective_expr())
print("Fewest number of connections between source and destination ",model.objective_expr()-1)

1 --> 3
3 --> 4
4 --> 17
13 --> 16
17 --> 20
20 --> 13
Shortest Path length:  6.0
Fewest number of connections between source and destination  5.0


### Large Network

In [76]:
#Create a Model
model = ConcreteModel()

#Variables
model.x = Var(range(n_individuals_large),range(n_individuals_large),within=Binary)

# Objective Function
objective_expr = 0
for i in range(n_individuals_large):
  for j in range(n_individuals_large):
    objective_expr += model.x[i,j]*adj_mat_large[i,j]

model.objective_expr = Objective(expr=objective_expr,sense=minimize)

# Constraints
# There cannot exist a path between nodes that are not connected
model.does_not_exist_constraints = ConstraintList()
for i in range(n_individuals_large):
  for j in range(n_individuals_large):
    if adj_mat_large[i,j] < 0.001:
      model.does_not_exist_constraints.add(model.x[i,j] == 0)

#Node flow constraints
#for all the intermediate nodes : number of outgoing edges - number of incoming edges = 0
# for source node : number of outgoing edges - number of incoming edges = 1
# for destination node : number of outgoing edges - number of incoming edges = -1
model.node_flow = ConstraintList()
for i in range(n_individuals_large):
  node_incoming_total = 0
  node_outgoing_total = 0
  for j in range(n_individuals_large):
    node_outgoing_total += model.x[i,j]
    node_incoming_total += model.x[j,i]
  if i==source_node:
    model.node_flow.add(node_outgoing_total-node_incoming_total == 1)
  elif i==destination_node:
    model.node_flow.add(node_outgoing_total-node_incoming_total == -1)
  else:
    model.node_flow.add(node_outgoing_total-node_incoming_total == 0)


model.pprint()

SolverFactory('cbc').solve(model, tee=True).write()

5 Set Declarations
    does_not_exist_constraints_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any : 2300 : {1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183, 184, 185, 

In [77]:
#print the shortest path from source to destination
for i in range(n_individuals_large):
  for j in range(n_individuals_large):
    if model.x[i,j]() > 0.5:
      print(i+1, "-->", j+1)
print("Shortest Path length: ",model.objective_expr())
print("Fewest number of connections between source and destination ",model.objective_expr()-1)

1 --> 2
2 --> 16
Shortest Path length:  2.0
Fewest number of connections between source and destination  1.0


# Problem 1.c - Diversity
* Size of largest group of people no two of which are connected to each other



### Small Network

In [78]:
#Create a Model
model = ConcreteModel()

#Variables - 0/1 variable indicating whether each of the user is in the diverse group or not
model.x = Var(range(n_individuals_small),within=Binary)

# Objective Function
objective_expr = 0
for i in range(n_individuals_small):
    objective_expr += model.x[i]

model.objective_expr = Objective(expr=objective_expr,sense=maximize)

# Constraints
# Any two nodes should not be directly connected to each other in a diverse group
# if a node is present, all its connected nodes should not be present in the group
model.connected_nodes = ConstraintList()
for i in range(n_individuals_small):
  sum_connected_nodes_expr =0
  total_connected_nodes = 0
  for j in range(n_individuals_small):
    sum_connected_nodes_expr += model.x[j]*adj_mat_small[i][j]
    total_connected_nodes += adj_mat_small[i][j]
  model.connected_nodes.add(sum_connected_nodes_expr <= total_connected_nodes*(1-model.x[i]))
  

model.pprint()

SolverFactory('cbc').solve(model, tee=True).write()#couenne

2 Set Declarations
    connected_nodes_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :   20 : {1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20}
    x_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :   20 : {0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19}

1 Var Declarations
    x : Size=20, Index=x_index
        Key : Lower : Value : Upper : Fixed : Stale : Domain
          0 :     0 :  None :     1 : False :  True : Binary
          1 :     0 :  None :     1 : False :  True : Binary
          2 :     0 :  None :     1 : False :  True : Binary
          3 :     0 :  None :     1 : False :  True : Binary
          4 :     0 :  None :     1 : False :  True : Binary
          5 :     0 :  None :     1 : False :  True : Binary
          6 :     0 :  None :     1 : False :  True : Binary
         

In [79]:
#print the members of largest diverse group - Small Network
for i in range(n_individuals_small):
  if model.x[i]() > 0.5:
    print(i+1, end="\t")
print("\n")
print("Size of largest diverse group: ",model.objective_expr())

2	4	5	9	11	15	18	19	

Size of largest diverse group:  8.0


### Large Network

In [80]:
#Create a Model
model = ConcreteModel()

#Variables - 0/1 variable indicating whether each of the user is in the diverse group or not
model.x = Var(range(n_individuals_large),within=Binary)

# Objective Function
objective_expr = 0
for i in range(n_individuals_large):
    objective_expr += model.x[i]

model.objective_expr = Objective(expr=objective_expr,sense=maximize)

# Constraints
# Any two nodes should not be directly connected to each other in a diverse group
# if a node is present, all its connected nodes should not be present in the group
model.connected_nodes = ConstraintList()
for i in range(n_individuals_large):
  sum_connected_nodes_expr =0
  total_connected_nodes = 0
  for j in range(n_individuals_large):
    sum_connected_nodes_expr += model.x[j]*adj_mat_large[i][j]
    total_connected_nodes += adj_mat_large[i][j]
  model.connected_nodes.add(sum_connected_nodes_expr <= total_connected_nodes*(1-model.x[i]))
  

model.pprint()

SolverFactory('cbc').solve(model, tee=True).write()#couenne

2 Set Declarations
    connected_nodes_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :   50 : {1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50}
    x_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :   50 : {0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49}

1 Var Declarations
    x : Size=50, Index=x_index
        Key : Lower : Value : Upper : Fixed : Stale : Domain
          0 :     0 :  None :     1 : False :  True : Binary
          1 :     0 :  None :     1 : False :  True : Binary
          2 :     0 :  None :     1 : False :  True : Binary
          3 :

In [81]:
#print the members of largest diverse group - Large Network
for i in range(n_individuals_large):
  if model.x[i]() > 0.5:
    print(i+1, end="\t")
print("\n")
print("Size of largest diverse group: ",model.objective_expr())

4	6	8	11	15	17	18	21	24	26	29	30	31	35	38	40	42	45	47	49	

Size of largest diverse group:  20.0


# Problem 1.d - Cliques
* Size of largest group of people, all of whom know each other

### Small Network

In [82]:
#Create a Model
model = ConcreteModel()

#Variables - 0/1 variable indicating whether each of the user is in the clique or not
model.x = Var(range(n_individuals_small),within=Binary)

# Objective Function
objective_expr = 0
for i in range(n_individuals_small):
    objective_expr += model.x[i]

model.objective_expr = Objective(expr=objective_expr,sense=maximize)

# Constraints
# Any two nodes should  be directly connected to each other in a clique
# if a node is present, all its non-connected nodes should not be present in the clique
model.non_connected_nodes = ConstraintList()
for i in range(n_individuals_small):
  sum_non_connected_nodes_expr =0
  total_non_connected_nodes = 0
  for j in range(n_individuals_small):
    if j!= i:
      sum_non_connected_nodes_expr += model.x[j]*(1-adj_mat_small[i][j])
      total_non_connected_nodes += (1-adj_mat_small[i][j])
  model.non_connected_nodes.add(sum_non_connected_nodes_expr <= total_non_connected_nodes*(1-model.x[i]))
  

model.pprint()

SolverFactory('cbc').solve(model, tee=True).write()

2 Set Declarations
    non_connected_nodes_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :   20 : {1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20}
    x_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :   20 : {0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19}

1 Var Declarations
    x : Size=20, Index=x_index
        Key : Lower : Value : Upper : Fixed : Stale : Domain
          0 :     0 :  None :     1 : False :  True : Binary
          1 :     0 :  None :     1 : False :  True : Binary
          2 :     0 :  None :     1 : False :  True : Binary
          3 :     0 :  None :     1 : False :  True : Binary
          4 :     0 :  None :     1 : False :  True : Binary
          5 :     0 :  None :     1 : False :  True : Binary
          6 :     0 :  None :     1 : False :  True : Binary
     

In [83]:
#print the members of largest clique - Small network
for i in range(n_individuals_small):
  if model.x[i]() > 0.5:
    print(i+1, end="\t")
print("\n")
print("size of largest clique: ",model.objective_expr())

13	14	18	

size of largest clique:  3.0


### Other cliques of same size within the network

In [84]:
# Adding constraints to not select the optimal solution selected thus far, but have same optimal value
optimal_value = model.objective_expr()
model.solution_constraint = ConstraintList()
while True:
  sum_solution_expr = 0
  for i in range(n_individuals_small):
    if model.x[i]() > 0.5:
      sum_solution_expr += model.x[i]
    else:
      sum_solution_expr += (1-model.x[i])
  model.solution_constraint.add(sum_solution_expr<=n_individuals_small - 1)
  SolverFactory('cbc').solve(model, tee=False)#.write()
  if (model.objective_expr() < optimal_value-0.5):
    break
  for i in range(n_individuals_small):
    if model.x[i]() > 0.5:
      print(i+1, end="\t")
  print("\n")
  print("size of this clique: ",model.objective_expr())



17	19	20	

size of this clique:  3.0
9	10	12	

size of this clique:  3.0
10	11	12	

size of this clique:  3.0
1	2	3	

size of this clique:  3.0
5	6	7	

size of this clique:  3.0
13	14	16	

size of this clique:  3.0
13	18	20	

size of this clique:  3.0


### Large Network

In [85]:
#Create a Model
model = ConcreteModel()

#Variables - 0/1 variable indicating whether each of the user is in the clique or not
model.x = Var(range(n_individuals_large),within=Binary)

# Objective Function
objective_expr = 0
for i in range(n_individuals_large):
    objective_expr += model.x[i]

model.objective_expr = Objective(expr=objective_expr,sense=maximize)

# Constraints
# Any two nodes should  be directly connected to each other in a clique
# if a node is present, all its non-connected nodes should not be present in the clique
model.non_connected_nodes = ConstraintList()
for i in range(n_individuals_large):
  sum_non_connected_nodes_expr =0
  total_non_connected_nodes = 0
  for j in range(n_individuals_large):
    if j!= i:
      sum_non_connected_nodes_expr += model.x[j]*(1-adj_mat_large[i][j])
      total_non_connected_nodes += (1-adj_mat_large[i][j])
  model.non_connected_nodes.add(sum_non_connected_nodes_expr <= total_non_connected_nodes*(1-model.x[i]))
  

model.pprint()

SolverFactory('cbc').solve(model, tee=True).write()

2 Set Declarations
    non_connected_nodes_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :   50 : {1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50}
    x_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :   50 : {0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49}

1 Var Declarations
    x : Size=50, Index=x_index
        Key : Lower : Value : Upper : Fixed : Stale : Domain
          0 :     0 :  None :     1 : False :  True : Binary
          1 :     0 :  None :     1 : False :  True : Binary
          2 :     0 :  None :     1 : False :  True : Binary
         

In [86]:
#print the members of largest clique - Large network
for i in range(n_individuals_large):
  if model.x[i]() > 0.5:
    print(i+1, end="\t")
print("\n")
print("size of largest clique: ",model.objective_expr())

36	37	39	40	

size of largest clique:  4.0


### Other cliques of same size within the network

In [87]:
# Adding constraints to not select the optimal solution thus far, but have same optimal value
optimal_value = model.objective_expr()
model.solution_constraint = ConstraintList()
while True:
  sum_solution_expr = 0
  for i in range(n_individuals_large):
    if model.x[i]() > 0.5:
      sum_solution_expr += model.x[i]
    else:
      sum_solution_expr += (1-model.x[i])
  model.solution_constraint.add(sum_solution_expr<=n_individuals_large - 1)
  SolverFactory('cbc').solve(model, tee=False)#.write()
  if (model.objective_expr() < optimal_value-0.5):
    break
  for i in range(n_individuals_large):
    if model.x[i]() > 0.5:
      print(i+1, end="\t")
  print("\n")
  print("size of this clique: ",model.objective_expr())



41	43	44	45	

size of this clique:  4.0


# Problem 2.a - Linkedin Premium free trial
* fewest number of people to be offered a trial such that every individual is connected to atleast one person who is offered a trial

### Small network

In [88]:
#Create a Model
model = ConcreteModel()

#Variables - 0/1 variable indicating whether each of the user is given a free trial or not
model.x = Var(range(n_individuals_small),within=Binary)

# Objective Function
objective_expr = 0
for i in range(n_individuals_small):
    objective_expr += model.x[i]

model.objective_expr = Objective(expr=objective_expr,sense=minimize)

# Constraints
# if a node is not given a free trial, atleast one of its connected nodes should be given a free trial
model.connected_nodes = ConstraintList()
for i in range(n_individuals_small):
  sum_connected_nodes_expr =0
  total_connected_nodes = 0
  for j in range(n_individuals_small):
    sum_connected_nodes_expr += model.x[j]*adj_mat_small[i][j]
    total_connected_nodes += adj_mat_small[i][j]
  model.connected_nodes.add(sum_connected_nodes_expr <= total_connected_nodes*(1-model.x[i]))
  model.connected_nodes.add(sum_connected_nodes_expr >= (1-model.x[i]))
  

model.pprint()

SolverFactory('cbc').solve(model, tee=True).write()

2 Set Declarations
    connected_nodes_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :   40 : {1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40}
    x_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :   20 : {0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19}

1 Var Declarations
    x : Size=20, Index=x_index
        Key : Lower : Value : Upper : Fixed : Stale : Domain
          0 :     0 :  None :     1 : False :  True : Binary
          1 :     0 :  None :     1 : False :  True : Binary
          2 :     0 :  None :     1 : False :  True : Binary
          3 :     0 :  None :     1 : False :  True : Binary
          4 :     0 :  None :     1 : False :  True : Binary
          5 :     0 :  None :     1 : False :  True

In [89]:
#print the users who should be offered a free trial so that everyone is else connected to atleast one user with free trial 
for i in range(n_individuals_small):
  if model.x[i]() > 0.5:
    print(i+1, end="\t")
print("\n")
print("fewest number of people to be offered linkedin free trial ",model.objective_expr())

3	7	12	16	20	

fewest number of people to be offered linkedin free trial  5.0


### Large Network

In [90]:
#Create a Model
model = ConcreteModel()

#Variables - 0/1 variable indicating whether each of the user is given a free trial or not
model.x = Var(range(n_individuals_large),within=Binary)

# Objective Function
objective_expr = 0
for i in range(n_individuals_large):
    objective_expr += model.x[i]

model.objective_expr = Objective(expr=objective_expr,sense=minimize)

# Constraints
# if a node is not given a free trial, atleast one of its connected nodes should be given a free trial
model.connected_nodes = ConstraintList()
for i in range(n_individuals_large):
  sum_connected_nodes_expr =0
  total_connected_nodes = 0
  for j in range(n_individuals_large):
    sum_connected_nodes_expr += model.x[j]*adj_mat_large[i][j]
    total_connected_nodes += adj_mat_large[i][j]
  model.connected_nodes.add(sum_connected_nodes_expr <= total_connected_nodes*(1-model.x[i]))
  model.connected_nodes.add(sum_connected_nodes_expr >= (1-model.x[i]))
  

model.pprint()

SolverFactory('cbc').solve(model, tee=True).write()

2 Set Declarations
    connected_nodes_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :  100 : {1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100}
    x_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :   50 : {0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49}

1 Var Declarations
    x : Size=50, Index=x_index
        Key : Lower : Value : Upper : Fixed : Stale : Do

In [91]:
#print the users who should be offered a free trial so that everyone is else connected to atleast one user with free trial 
for i in range(n_individuals_large):
  if model.x[i]() > 0.5:
    print(i+1, end="\t")
print("\n")
print("fewest number of people to be offered linkedin free trial ",model.objective_expr())

5	7	13	16	20	25	28	35	39	41	50	

fewest number of people to be offered linkedin free trial  11.0


# Problem 2.b
* Given that only two free trials are available, which are two best people to offer, maximize number of people connected to those two people

### Small Network

In [92]:
#Create a Model
model = ConcreteModel()

#Variables - 0/1 variable indicating whether each pair of nodes is chosen to be given a free trial or not
model.x = Var(range(n_individuals_small),range(n_individuals_small),within=Binary)

# Objective Function - total number of distinctly connected nodes to the selected node pair 
#pre-calculate a matrix connectedness, of shape n_individuals_small x n_individuals_small where connectedness[i,j] contains total number of distinctly connected
#nodes to node_i and node_j (excluding  node_i , node_j)
connectedness  = np.zeros((n_individuals_small,n_individuals_small))
for i in range(n_individuals_small):
  for j in range(n_individuals_small):
    if j!=i:
      connectedness[i,j] = sum(adj_mat_small[i]) + sum(adj_mat_small[j]) - 2*adj_mat_small[i,j] - np.dot(adj_mat_small[i],adj_mat_small[j])
objective_expr = 0
for i in range(n_individuals_small):
  for j in range(n_individuals_small):
    objective_expr += model.x[i,j]*connectedness[i,j]

model.objective_expr = Objective(expr=objective_expr,sense=maximize)

# Constraints
# Only two individuals can be offered free trial
# same individual cannot be offered two free trials
model.budget_constraint =  ConstraintList()
sum_free_trial_users = 0
same_users_expr = 0
for i in range(n_individuals_small):
  for j in range(n_individuals_small):
    sum_free_trial_users += model.x[i,j]
  same_users_expr += model.x[i,i]

model.budget_constraint.add(sum_free_trial_users == 1)
model.budget_constraint.add(same_users_expr == 0)


model.pprint()

SolverFactory('cbc').solve(model, tee=True).write()

4 Set Declarations
    budget_constraint_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :    2 : {1, 2}
    x_index : Size=1, Index=None, Ordered=True
        Key  : Dimen : Domain              : Size : Members
        None :     2 : x_index_0*x_index_1 :  400 : {(0, 0), (0, 1), (0, 2), (0, 3), (0, 4), (0, 5), (0, 6), (0, 7), (0, 8), (0, 9), (0, 10), (0, 11), (0, 12), (0, 13), (0, 14), (0, 15), (0, 16), (0, 17), (0, 18), (0, 19), (1, 0), (1, 1), (1, 2), (1, 3), (1, 4), (1, 5), (1, 6), (1, 7), (1, 8), (1, 9), (1, 10), (1, 11), (1, 12), (1, 13), (1, 14), (1, 15), (1, 16), (1, 17), (1, 18), (1, 19), (2, 0), (2, 1), (2, 2), (2, 3), (2, 4), (2, 5), (2, 6), (2, 7), (2, 8), (2, 9), (2, 10), (2, 11), (2, 12), (2, 13), (2, 14), (2, 15), (2, 16), (2, 17), (2, 18), (2, 19), (3, 0), (3, 1), (3, 2), (3, 3), (3, 4), (3, 5), (3, 6), (3, 7), (3, 8), (3, 9), (3, 10), (3, 11), (3, 12), (3, 13), (3, 14), (3, 15), (3, 16), (3, 17)

In [93]:
#print two best users that need to be offered a free trial
for i in range(n_individuals_small):
  for j in range(n_individuals_small):
    if model.x[i,j]() > 0.5:
      print(i+1, "\t", j+1)
print("Number of connections covered by offering these two free trials: ",model.objective_expr())

9 	 20
Number of connections covered by offering these two free trials:  9.0


### Large Network

In [94]:
#Create a Model
model = ConcreteModel()

#Variables - 0/1 variable indicating whether each pair of nodes is chosen to be given a free trial or not
model.x = Var(range(n_individuals_large),range(n_individuals_large),within=Binary)

# Objective Function - total number of distinctly connected nodes to the selected node pair 
#pre-calculate a matrix connectedness, of shape n_individuals x n_individuals where connectedness[i,j] contains total number of distinctly connected
#nodes to node_i and node_j (excluding  node_i , node_j)
connectedness  = np.zeros((n_individuals_large,n_individuals_large))
for i in range(n_individuals_large):
  for j in range(n_individuals_large):
    if j!=i:
      connectedness[i,j] = sum(adj_mat_large[i]) + sum(adj_mat_large[j]) - 2*adj_mat_large[i,j] - np.dot(adj_mat_large[i],adj_mat_large[j])
objective_expr = 0
for i in range(n_individuals_large):
  for j in range(n_individuals_large):
    objective_expr += model.x[i,j]*connectedness[i,j]

model.objective_expr = Objective(expr=objective_expr,sense=maximize)

# Constraints
# Only two individuals can be offered free trial
# same individual cannot be offered two free trials
model.budget_constraint =  ConstraintList()
sum_free_trial_users = 0
same_users_expr = 0
for i in range(n_individuals_large):
  for j in range(n_individuals_large):
    sum_free_trial_users += model.x[i,j]
  same_users_expr += model.x[i,i]

model.budget_constraint.add(sum_free_trial_users == 1)
model.budget_constraint.add(same_users_expr == 0)


model.pprint()

SolverFactory('cbc').solve(model, tee=True).write()

4 Set Declarations
    budget_constraint_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :    2 : {1, 2}
    x_index : Size=1, Index=None, Ordered=True
        Key  : Dimen : Domain              : Size : Members
        None :     2 : x_index_0*x_index_1 : 2500 : {(0, 0), (0, 1), (0, 2), (0, 3), (0, 4), (0, 5), (0, 6), (0, 7), (0, 8), (0, 9), (0, 10), (0, 11), (0, 12), (0, 13), (0, 14), (0, 15), (0, 16), (0, 17), (0, 18), (0, 19), (0, 20), (0, 21), (0, 22), (0, 23), (0, 24), (0, 25), (0, 26), (0, 27), (0, 28), (0, 29), (0, 30), (0, 31), (0, 32), (0, 33), (0, 34), (0, 35), (0, 36), (0, 37), (0, 38), (0, 39), (0, 40), (0, 41), (0, 42), (0, 43), (0, 44), (0, 45), (0, 46), (0, 47), (0, 48), (0, 49), (1, 0), (1, 1), (1, 2), (1, 3), (1, 4), (1, 5), (1, 6), (1, 7), (1, 8), (1, 9), (1, 10), (1, 11), (1, 12), (1, 13), (1, 14), (1, 15), (1, 16), (1, 17), (1, 18), (1, 19), (1, 20), (1, 21), (1, 22), (1, 23), (1, 24), (1, 2

In [95]:
#print two best users that need to be offered a free trial
for i in range(n_individuals_large):
  for j in range(n_individuals_large):
    if model.x[i,j]() > 0.5:
      print(i+1, "\t", j+1)
print("\n")
print("Number of connections covered by offering these two free trials: ",model.objective_expr())

12 	 25


Number of connections covered by offering these two free trials:  15.0


# Problem 3 - Cluster Analysis

### Small Network

In [96]:
#Create a Model
model = ConcreteModel()

# Variables x (n_clusters, n_individuals) - binary variable indicates whether a user is a part of a cluster or not
# y - indicates whether there exists an element in that cluster or not 
n_clusters = n_individuals_small
model.x = Var(range(n_clusters),range(n_individuals_small),within=Binary)
model.y = Var(range(n_clusters),within=Binary)

# Objective Function
objective_expr = 0
for i in range(n_clusters):
    objective_expr += model.y[i]

model.objective_expr = Objective(expr=objective_expr,sense=minimize)

# Constraints
# Each node should be there in exactly one cluster
model.cluster_individual = ConstraintList()

for j in range(n_individuals_small):
  cluster_per_individual_expr = 0
  for i in range(n_clusters):
    cluster_per_individual_expr += model.x[i,j]
  model.cluster_individual.add(cluster_per_individual_expr == 1)

# Each cluster can have only those nodes that are all connected to each other 
# For all the clusters, if a node is present in a cluster, all the incompatible nodes cannot be present in the same cluster
model.connected_cluster = ConstraintList()
for i in range(n_clusters):
  for j in range(n_individuals_small):
    incompatible_nodes = sum([adj_mat_small[j,k]*model.x[i,k] for k in range(n_individuals_small)])
    model.connected_cluster.add(model.x[i,j]<= 1- incompatible_nodes)

#channeling constraints
# y[i] = 1 if there is atleast one element in the cluster,  0 otherwise
model.chanelling_constraint = ConstraintList()
nodes_in_cluster_expr = 0
for i in range(n_clusters):
  for j in range(n_individuals_small):
    nodes_in_cluster_expr += model.x[i,j]
  model.chanelling_constraint.add(nodes_in_cluster_expr>=model.y[i])
  model.chanelling_constraint.add(nodes_in_cluster_expr<=n_individuals_small*model.y[i])

model.pprint()

SolverFactory('cbc').solve(model, tee=True).write()

7 Set Declarations
    chanelling_constraint_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :   40 : {1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40}
    cluster_individual_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :   20 : {1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20}
    connected_cluster_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :  400 : {1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75

In [97]:
#print cluster number and users assigned to each cluster
for i in range(n_clusters):
  if model.y[i]() > 0.5:
    print (i+1, end=":\t")
    for j in range(n_individuals_small):
      if model.x[i,j]() > 0.5:
        print(j+1, end="\t")
    print("\n")
print("Minimum number of clusters such that every person in the cluster is linked to each other: ",model.objective_expr())

15:	9	

16:	10	20	

17:	2	6	13	

18:	1	5	16	17	

19:	4	7	12	15	18	

20:	3	8	11	14	19	

Minimum number of clusters such that every person in the cluster is linked to each other:  6.0


### Large network

In [98]:
#Create a Model
model = ConcreteModel()

# Variables x (n_clusters, n_individuals) - binary variable indicates whether a user is a part of a cluster or not
# y - indicates whether there exists an element in that cluster or not 
n_clusters = n_individuals_large
model.x = Var(range(n_clusters),range(n_individuals_large),within=Binary)
model.y = Var(range(n_clusters),within=Binary)

# Objective Function
objective_expr = 0
for i in range(n_clusters):
    objective_expr += model.y[i]

model.objective_expr = Objective(expr=objective_expr,sense=minimize)

# Constraints
# Each node should be there in exactly one cluster
model.cluster_individual = ConstraintList()

for j in range(n_individuals_large):
  cluster_per_individual_expr = 0
  for i in range(n_clusters):
    cluster_per_individual_expr += model.x[i,j]
  model.cluster_individual.add(cluster_per_individual_expr == 1)

# Each cluster can have only those nodes that are all connected to each other 
# For all the clusters, if a node is present in a cluster, all the incompatible nodes cannot be present in the same cluster
model.connected_cluster = ConstraintList()
for i in range(n_clusters):
  for j in range(n_individuals_large):
    incompatible_nodes = sum([adj_mat_large[j,k]*model.x[i,k] for k in range(n_individuals_large)])
    model.connected_cluster.add(model.x[i,j]<= 1- incompatible_nodes)

#channeling constraints
# y[i] = 1 if there is atleast one element in the cluster,  0 otherwise
model.chanelling_constraint = ConstraintList()
nodes_in_cluster_expr = 0
for i in range(n_clusters):
  for j in range(n_individuals_large):
    nodes_in_cluster_expr += model.x[i,j]
  model.chanelling_constraint.add(nodes_in_cluster_expr>=model.y[i])
  model.chanelling_constraint.add(nodes_in_cluster_expr<=n_individuals_large*model.y[i])

model.pprint()

SolverFactory('cbc').solve(model, tee=True).write()

7 Set Declarations
    chanelling_constraint_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :  100 : {1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100}
    cluster_individual_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :   50 : {1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50}
    connected_cluster_index : Size=1, Index=None, Ordered=Insertion
        Key  : 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Welcome to the CBC MILP Solver 
Version: 2.10.8 
Build Date: Mar 31 2023 

command line - /content/bin/cbc -printingOptions all -import /tmp/tmpq74j8xj9.pyomo.lp -stat=1 -solve -solu /tmp/tmpq74j8xj9.pyomo.soln (default strategy 1)
Option for printingOptions changed from normal to all
Presolve 2548 (-102) rows, 2549 (-1) columns and 137198 (-5402) elements
Statistics for presolved model
Original problem has 2550 integers (2550 of which binary)
Presolved problem has 2549 integers (2549 of which binary)
==== 2500 zero objective 2 different
2500 variables have objective of 0
49 variables have objective of 1
==== absolute objective values 2 different
2500 variables have objective of 0
49 variables have objective of 1
==== for integers 2500 zero objective 2 different
2500 variables have objective of 0
49 variables have objective of 1
==== for integers absolute objective values 2 different
2500 variables have objective of 0
49 variables have objective of 1
===== end objective counts


Proble

In [99]:
#print cluster number and users assigned to each cluster
for i in range(n_clusters):
  if model.y[i]() > 0.5:
    print (i+1, end=":\t")
    for j in range(n_individuals_large):
      if model.x[i,j]() > 0.5:
        print(j+1, end="\t")
    print("\n")
print("\n")
print("Minimum number of clusters such that every person in the cluster is linked to each other: ",model.objective_expr())

42:	2	11	31	37	

43:	12	38	41	

44:	22	26	49	

45:	20	21	27	46	

46:	9	33	39	42	47	

47:	1	6	10	15	19	28	35	43	

48:	3	13	24	29	32	36	44	48	

49:	4	7	14	16	18	25	

50:	5	8	17	23	30	34	40	45	50	



Minimum number of clusters such that every person in the cluster is linked to each other:  9.0
